In [1]:
!pip install crewai==0.28.8 crewai_tools==0.1.6 langchain_community==0.0.29

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.9/40.9 kB 2.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 4.2 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.3/67.3 kB 4.8 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
INFO: pip is looking at multiple versions of embedchain to determine which version is compatible with other requirements. This could take a while.
INFO: pip is still looking at multiple versions of embedchain to determine which version is compatible with other requirements. This could take a while.
INFO: This is taking longer than usual. You might need to provide the dependency resolver with stricter constraints to reduce runtime. See https://pip.pypa.io/warnings/backtracking for guida

In [1]:
import os

from crewai_tools import tool, SerperDevTool, ScrapeWebsiteTool, WebsiteSearchTool
from crewai import Agent, Task, Crew, Process
from langchain_openai import ChatOpenAI

/usr/local/lib/python3.12/dist-packages/pydantic/_internal/_generate_schema.py:918: UserWarning: Mixing V1 models and V2 models (or constructs, like `TypeAdapter`) is not supported. Please upgrade `CrewAgentExecutor` to V2.
  warn(


In [2]:
# Função para ler a chave de API do OpenAI
def get_openai_api_key():
    with open('API_OpenAI_SEPEI.txt', 'r') as file:
        return file.read().strip()

# Função para ler a chave de API do Serper
def get_serper_api_key():
    with open('API_Serper.txt', 'r') as file:
        return file.read().strip()

# Configurar variáveis de ambiente
openai_api_key = get_openai_api_key()
serper_api_key = get_serper_api_key()

os.environ["OPENAI_API_KEY"] = openai_api_key
os.environ["SERPER_API_KEY"] = serper_api_key


In [3]:
# Modelo LLM
gpt4o_mini_llm = ChatOpenAI(model="gpt-4o-mini", api_key=openai_api_key)

# Ferramentas
ferramenta_de_busca = SerperDevTool()
ferramenta_de_raspagem = ScrapeWebsiteTool()

In [4]:
planejador = Agent(
    role="Planejador de Conteúdo",
    goal="Planejar conteúdo envolvente e factualmente preciso sobre {tópico}",
    backstory=(
        "Você está trabalhando no planejamento de um artigo de blog "
        "sobre o tópico: {tópico}. "
        "Você coleta informações que ajudam o público a aprender algo "
        "e tomar decisões informadas. "
        "Seu trabalho é a base para que o Redator de Conteúdo escreva "
        "um artigo sobre este tópico."
    ),
    verbose=True,
    tools=[ferramenta_de_busca, ferramenta_de_raspagem],
    allow_delegation=False,
    llm=gpt4o_mini_llm
)

escritor = Agent(
    role="Redator de Conteúdo",
    goal="Escrever um artigo em português do Brasil, de opinião perspicaz e factualmente preciso sobre {tópico}",
    backstory=(
        "Você está trabalhando na escrita de um artigo de opinião sobre o tópico: {tópico}. "
        "Você baseia sua escrita no trabalho do Planejador de Conteúdo, que fornece um esboço e contexto. "
        "Você segue os principais objetivos e fornece insights apoiados em informações do Planejador. "
        "Reconhece quando uma afirmação é opinião e quando é fato."
    ),
    verbose=True,
    tools=[ferramenta_de_busca, ferramenta_de_raspagem],
    allow_delegation=False,
    llm=gpt4o_mini_llm
)

editor = Agent(
    role="Editor",
    goal="Editar um post de blog alinhado ao estilo da organização.",
    backstory=(
        "Você é um editor que recebe um post de blog do Redator de Conteúdo. "
        "Seu objetivo é revisar para garantir boas práticas jornalísticas, "
        "apresentar pontos de vista equilibrados e evitar polêmicas desnecessárias."
    ),
    verbose=True,
    tools=[ferramenta_de_busca, ferramenta_de_raspagem],
    allow_delegation=False,
    llm=gpt4o_mini_llm
)


In [5]:
planejamento = Task(
    description=(
        "1. Priorizar as últimas tendências, principais players e notícias relevantes sobre {tópico}.\n"
        "2. Identificar o público-alvo, considerando interesses e pontos de dor.\n"
        "3. Desenvolver um esboço de conteúdo detalhado com introdução, pontos principais e call-to-action.\n"
        "4. Incluir palavras-chave de SEO e fontes relevantes."
    ),
    expected_output="Documento de plano de conteúdo com esboço, público-alvo, palavras-chave e recursos.",
    agent=planejador,
)

escrita = Task(
    description=(
        "1. Use o plano de conteúdo para criar um post de blog atraente sobre {tópico}.\n"
        "2. Incorpore palavras-chave de SEO de forma natural.\n"
        "3. Nomeie seções de maneira envolvente.\n"
        "4. Estruture com introdução, corpo e conclusão.\n"
        "5. Revise erros gramaticais e alinhe com público-alvo."
    ),
    expected_output="Post de blog em português, formato markdown, pronto para publicação.",
    agent=escritor,
)

edicao = Task(
    description="Revise o post de blog para corrigir erros e alinhar ao público-alvo.",
    expected_output="Post revisado, pronto para publicação, em português, com seções de 3-4 parágrafos.",
    agent=editor
)


In [6]:
crew = Crew(
    agents=[planejador, escritor, editor],
    tasks=[planejamento, escrita, edicao],
    verbose=2
)


In [ ]:
result = crew.kickoff(inputs={"tópico": "Seminário de Ensino, Pesquisa e Extensão do IFSC - SEPEI"})

from IPython.display import Markdown
Markdown(result)


 [DEBUG]: == Working Agent: Planejador de Conteúdo
 [INFO]: == Starting Task: 1. Priorizar as últimas tendências, principais players e notícias relevantes sobre Seminário de Ensino, Pesquisa e Extensão do IFSC - SEPEI.
2. Identificar o público-alvo, considerando interesses e pontos de dor.
3. Desenvolver um esboço de conteúdo detalhado com introdução, pontos principais e call-to-action.
4. Incluir palavras-chave de SEO e fontes relevantes.


> Entering new CrewAgentExecutor chain...
Action: Search the internet  
Action Input: {"search_query": "Seminário de Ensino, Pesquisa e Extensão do IFSC - SEPEI 2023"}   


Search results: Title: Home | SEPEI 2023 - Galoá
Link: https://eventos.galoa.com.br/sepei-2023/page/2381-home
Snippet: O Seminário ocorrerá de 17 a 19 de abril de 2023, em formato híbrido, de forma presencial em Joinville, com parte de sua programação realizada de forma on-line ...
---
Title: sepei 2023 - Galoá Proceedings
Link: https://proceedings.science/sepei-2023
Snippet: O 